In [1]:
# import necessary libraries
import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, func, MetaData, Table
import pandas as pd
import numpy as np
import json

In [2]:
# Database Setup
engine = create_engine('sqlite:///SevereWeather.sqlite', echo=False)

In [3]:
# produce our own MetaData object
metadata = MetaData()

# we can reflect it ourselves from a database, using options
# such as 'only' to limit what tables we look at...
metadata.reflect(engine)

Base = automap_base()
Base.prepare(engine, reflect=True)

In [4]:
#Base.metadata.tables

In [5]:
#metadata.tables.keys()

In [6]:
from sqlalchemy import inspect
inspector = inspect(engine)

In [7]:
Events = Table('Events',metadata)
inspector.reflecttable(Events, None)
session = Session(bind=engine)

In [8]:
events_df = pd.read_sql_table('Events', engine)
events_df.head()

level_0  index    yr  mo  dy  st  mag  inj  fat  loss  closs     slat  \
0        0      0  2010   1  18  CA  0.0    0    0  0.00    0.0  36.7300   
1        1      1  2010   1  19  CA  0.0    0    0  0.00    0.0  34.4248   
2        2      2  2010   1  19  CA  1.0    0    0  0.50    0.0  33.7160   
3        3      3  2010   1  20  LA  0.0    0    0  0.00    0.0  30.8150   
4        4      4  2010   1  20  TX  1.0    0    0  0.04    0.0  31.5095   

       slon  type           date_time  
0 -119.8600  torn 2010-01-18 17:24:00  
1 -119.8770  torn 2010-01-19 12:32:00  
2 -118.1250  torn 2010-01-19 14:55:00  
3  -92.0455  torn 2010-01-20 15:27:00  
4  -93.9232  torn 2010-01-20 16:26:00

In [9]:
events_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 197287 entries, 0 to 197286
Data columns (total 15 columns):
level_0      197287 non-null int64
index        197287 non-null int64
yr           197287 non-null int64
mo           197287 non-null int64
dy           197287 non-null int64
st           197287 non-null object
mag          197287 non-null float64
inj          197287 non-null int64
fat          197287 non-null int64
loss         197287 non-null float64
closs        197287 non-null float64
slat         197287 non-null float64
slon         197287 non-null float64
type         197287 non-null object
date_time    197287 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(5), int64(7), object(2)
memory usage: 22.6+ MB


## Getting each type of storm in a dataframe.

In [10]:
# print(inspector.get_table_names())
# cols = print(inspector.get_columns('Events'))
# from sqlalchemy import select
# tornados = select([Events]).where(Events.c.type == 'torn')
# conn = engine.connect()
# res = conn.execute(tornados)
# for row in res: 
#     print(row[2:3],row[6:7], row[11:13])
# tornados_by_yr = select([Events]).where(Events.c.type == 'torn')
# events = Events.columns.type
# events

In [11]:
torn_df = events_df.loc[events_df['type']=="torn"]
torn_df.head()

level_0  index    yr  mo  dy  st  mag  inj  fat  loss  closs     slat  \
0        0      0  2010   1  18  CA  0.0    0    0  0.00    0.0  36.7300   
1        1      1  2010   1  19  CA  0.0    0    0  0.00    0.0  34.4248   
2        2      2  2010   1  19  CA  1.0    0    0  0.50    0.0  33.7160   
3        3      3  2010   1  20  LA  0.0    0    0  0.00    0.0  30.8150   
4        4      4  2010   1  20  TX  1.0    0    0  0.04    0.0  31.5095   

       slon  type           date_time  
0 -119.8600  torn 2010-01-18 17:24:00  
1 -119.8770  torn 2010-01-19 12:32:00  
2 -118.1250  torn 2010-01-19 14:55:00  
3  -92.0455  torn 2010-01-20 15:27:00  
4  -93.9232  torn 2010-01-20 16:26:00

In [12]:
torn_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8096 entries, 0 to 172254
Data columns (total 15 columns):
level_0      8096 non-null int64
index        8096 non-null int64
yr           8096 non-null int64
mo           8096 non-null int64
dy           8096 non-null int64
st           8096 non-null object
mag          8096 non-null float64
inj          8096 non-null int64
fat          8096 non-null int64
loss         8096 non-null float64
closs        8096 non-null float64
slat         8096 non-null float64
slon         8096 non-null float64
type         8096 non-null object
date_time    8096 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(5), int64(7), object(2)
memory usage: 1012.0+ KB


In [13]:
tornado_mag_df = pd.DataFrame(torn_df, columns=['yr', 'mag', 'slat', 'slon'])
tornado_mag_df.head()

yr  mag     slat      slon
0  2010  0.0  36.7300 -119.8600
1  2010  0.0  34.4248 -119.8770
2  2010  1.0  33.7160 -118.1250
3  2010  0.0  30.8150  -92.0455
4  2010  1.0  31.5095  -93.9232

In [14]:
tornado_mag_df.max()

yr      2016.0000
mag        5.0000
slat      48.9832
slon       0.0000
dtype: float64

In [15]:
tornado_df = tornado_mag_df.reset_index()
tornado_df.head(10)

index    yr  mag     slat      slon
0      0  2010  0.0  36.7300 -119.8600
1      1  2010  0.0  34.4248 -119.8770
2      2  2010  1.0  33.7160 -118.1250
3      3  2010  0.0  30.8150  -92.0455
4      4  2010  1.0  31.5095  -93.9232
5      5  2010  3.0  32.4869  -94.1689
6      6  2010  3.0  32.4869  -94.1689
7      7  2010  2.0  32.5710  -95.8725
8      8  2010  3.0  32.5182  -94.0432
9      9  2010  0.0  31.7667  -93.2623

In [16]:
value = ['2010']
tornado_2010_df = tornado_df[tornado_df.yr.isin(value)]
tornado_2010_df.head()

index    yr  mag     slat      slon
0      0  2010  0.0  36.7300 -119.8600
1      1  2010  0.0  34.4248 -119.8770
2      2  2010  1.0  33.7160 -118.1250
3      3  2010  0.0  30.8150  -92.0455
4      4  2010  1.0  31.5095  -93.9232

In [17]:
tornado_2010_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1315 entries, 0 to 1314
Data columns (total 5 columns):
index    1315 non-null int64
yr       1315 non-null int64
mag      1315 non-null float64
slat     1315 non-null float64
slon     1315 non-null float64
dtypes: float64(3), int64(2)
memory usage: 61.6 KB


In [18]:
import folium

In [19]:
locations = tornado_2010_df[['slat', 'slon']]
locationlist = locations.values.tolist()
len(locationlist)
locationlist[5]

[32.4869, -94.1689]

In [20]:
map = folium.Map(location=[37.09, -95.71], zoom_start=3)
for point in range(0, len(locationlist)):
    folium.CircleMarker(locationlist[point]).add_to(map)
map

In [21]:
tornado_list = []
for row in tornado_df:
    tornado_df[["mag","slat", "slon"]])
    print(tornado_df[["mag","slat", "slon"]])

SyntaxError: invalid syntax (<ipython-input-21-d7522aac73f6>, line 3)

In [22]:
hail_df = events_df.loc[events_df['type']=="hail"]
hail_df.head()

level_0  index    yr  mo  dy  st   mag  inj  fat  loss  closs     slat  \
1315     1315   1315  2010  12  31  MS  1.75    0    0   0.0    0.0  33.2964   
1316     1316   1316  2010  12  31  MS  1.75    0    0   0.0    0.0  33.1591   
1317     1317   1317  2010  12  31  MS  1.75    0    0   0.0    0.0  33.9972   
1318     1318   1318  2010  12  31  MS  1.00    0    0   0.0    0.0  32.5300   
1319     1319   1319  2010  12  31  AR  1.00    0    0   0.0    0.0  35.6976   

         slon  type           date_time  
1315 -89.9870  hail 2010-12-31 22:40:00  
1316 -90.1933  hail 2010-12-31 22:25:00  
1317 -88.6277  hail 2010-12-31 22:20:00  
1318 -91.0200  hail 2010-12-31 22:20:00  
1319 -90.0508  hail 2010-12-31 21:50:00

In [23]:
hail_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 79895 entries, 1315 to 181639
Data columns (total 15 columns):
level_0      79895 non-null int64
index        79895 non-null int64
yr           79895 non-null int64
mo           79895 non-null int64
dy           79895 non-null int64
st           79895 non-null object
mag          79895 non-null float64
inj          79895 non-null int64
fat          79895 non-null int64
loss         79895 non-null float64
closs        79895 non-null float64
slat         79895 non-null float64
slon         79895 non-null float64
type         79895 non-null object
date_time    79895 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(5), int64(7), object(2)
memory usage: 9.8+ MB


In [24]:
hail_mag_df = pd.DataFrame(hail_df, columns=['yr', 'mag', 'slat', 'slon'])
hail_mag_df.head()

yr   mag     slat     slon
1315  2010  1.75  33.2964 -89.9870
1316  2010  1.75  33.1591 -90.1933
1317  2010  1.75  33.9972 -88.6277
1318  2010  1.00  32.5300 -91.0200
1319  2010  1.00  35.6976 -90.0508

In [25]:
print(hail_mag_df.max())
print()
print(hail_mag_df.min())

yr      2016.0
mag        8.0
slat      65.0
slon     -65.8
dtype: float64

yr      2010.000
mag        0.150
slat      18.030
slon    -159.351
dtype: float64


In [27]:
hail_df = hail_mag_df.reset_index()
hail_df.head()

index    yr   mag     slat     slon
0   1315  2010  1.75  33.2964 -89.9870
1   1316  2010  1.75  33.1591 -90.1933
2   1317  2010  1.75  33.9972 -88.6277
3   1318  2010  1.00  32.5300 -91.0200
4   1319  2010  1.00  35.6976 -90.0508

In [28]:
hail_2010_df = hail_df[hail_df.yr.isin(value)]
hail_2010_df.head()

index    yr   mag     slat     slon
0   1315  2010  1.75  33.2964 -89.9870
1   1316  2010  1.75  33.1591 -90.1933
2   1317  2010  1.75  33.9972 -88.6277
3   1318  2010  1.00  32.5300 -91.0200
4   1319  2010  1.00  35.6976 -90.0508

In [29]:
hail_2010_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10908 entries, 0 to 10907
Data columns (total 5 columns):
index    10908 non-null int64
yr       10908 non-null int64
mag      10908 non-null float64
slat     10908 non-null float64
slon     10908 non-null float64
dtypes: float64(3), int64(2)
memory usage: 511.3 KB


In [36]:
locations2 = hail_2010_df[['slat', 'slon']]
locationlist2 = locations2.values.tolist()
len(locationlist2)
locationlist2[5]

[35.5, -90.15]

In [37]:
map = folium.Map(location=[37.09, -95.71], zoom_start=3)
for point in range(0, len(locationlist2)):
    folium.CircleMarker(locationlist2[point]).add_to(map)
map

In [30]:
wind_df = events_df.loc[events_df['type']=="wind"]
wind_df.head()

level_0  index    yr  mo  dy  st   mag  inj  fat   loss  closs  \
12223    12223  12223  2010   1  18  CA  51.0    0    0  0.000    0.0   
12224    12224  12224  2010   1  18  CA  70.0    0    0  0.000    0.0   
12225    12225  12225  2010   1  19  CA  81.0    0    0  0.350    0.0   
12226    12226  12226  2010   1  19  CA  70.0    0    0  0.025    0.0   
12227    12227  12227  2010   1  19  CA  52.0    0    0  0.000    0.0   

          slat     slon  type           date_time  
12223  37.6200 -122.380  wind 2010-01-18 12:23:00  
12224  37.4411 -121.941  wind 2010-01-18 13:03:00  
12225  33.6533 -117.918  wind 2010-01-19 15:00:00  
12226  33.5263 -117.781  wind 2010-01-19 15:35:00  
12227  33.4104 -117.645  wind 2010-01-19 15:58:00

In [31]:
wind_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 109296 entries, 12223 to 197286
Data columns (total 15 columns):
level_0      109296 non-null int64
index        109296 non-null int64
yr           109296 non-null int64
mo           109296 non-null int64
dy           109296 non-null int64
st           109296 non-null object
mag          109296 non-null float64
inj          109296 non-null int64
fat          109296 non-null int64
loss         109296 non-null float64
closs        109296 non-null float64
slat         109296 non-null float64
slon         109296 non-null float64
type         109296 non-null object
date_time    109296 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(5), int64(7), object(2)
memory usage: 13.3+ MB


In [32]:
wind_mag_df = pd.DataFrame(wind_df, columns=['yr', 'mag', 'slat', 'slon'])
wind_mag_df.head()

yr   mag     slat     slon
12223  2010  51.0  37.6200 -122.380
12224  2010  70.0  37.4411 -121.941
12225  2010  81.0  33.6533 -117.918
12226  2010  70.0  33.5263 -117.781
12227  2010  52.0  33.4104 -117.645

In [33]:
print(wind_mag_df.max())
print()
print(wind_mag_df.min())

yr      2016.00
mag      131.00
slat      65.18
slon     -65.71
dtype: float64

yr      2010.0000
mag       30.0000
slat      17.9725
slon    -159.7800
dtype: float64


In [34]:
wind_2010_df = wind_df[wind_df.yr.isin(value)]
wind_2010_df.head()

level_0  index    yr  mo  dy  st   mag  inj  fat   loss  closs  \
12223    12223  12223  2010   1  18  CA  51.0    0    0  0.000    0.0   
12224    12224  12224  2010   1  18  CA  70.0    0    0  0.000    0.0   
12225    12225  12225  2010   1  19  CA  81.0    0    0  0.350    0.0   
12226    12226  12226  2010   1  19  CA  70.0    0    0  0.025    0.0   
12227    12227  12227  2010   1  19  CA  52.0    0    0  0.000    0.0   

          slat     slon  type           date_time  
12223  37.6200 -122.380  wind 2010-01-18 12:23:00  
12224  37.4411 -121.941  wind 2010-01-18 13:03:00  
12225  33.6533 -117.918  wind 2010-01-19 15:00:00  
12226  33.5263 -117.781  wind 2010-01-19 15:35:00  
12227  33.4104 -117.645  wind 2010-01-19 15:58:00

In [35]:
wind_2010_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 15503 entries, 12223 to 27725
Data columns (total 15 columns):
level_0      15503 non-null int64
index        15503 non-null int64
yr           15503 non-null int64
mo           15503 non-null int64
dy           15503 non-null int64
st           15503 non-null object
mag          15503 non-null float64
inj          15503 non-null int64
fat          15503 non-null int64
loss         15503 non-null float64
closs        15503 non-null float64
slat         15503 non-null float64
slon         15503 non-null float64
type         15503 non-null object
date_time    15503 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(5), int64(7), object(2)
memory usage: 1.9+ MB


In [ ]:
locations3 = hail_2010_df[['slat', 'slon']]
locationlist3 = locations3.values.tolist()
len(locationlist3)
locationlist2[5]

In [ ]:
map = folium.Map(location=[37.09, -95.71], zoom_start=3)
for point in range(0, len(locationlist3)):
    folium.CircleMarker(locationlist3[point]).add_to(map)
map